In [1]:
import folium
from folium import Choropleth
import geopandas as gpd
import pandas as pd
import numpy as np
import branca.colormap as cm

In [3]:
pd.__version__

'0.25.3'

In [2]:
dati_pr = pd.read_csv('https://raw.githubusercontent.com/pcm-dpc/COVID-19/master/dati-province/dpc-covid19-ita-province.csv')
dati_reg = pd.read_csv('https://raw.githubusercontent.com/pcm-dpc/COVID-19/master/dati-regioni/dpc-covid19-ita-regioni.csv')
regioni = gpd.read_file("https://raw.githubusercontent.com/openpolis/geojson-italy/master/geojson/limits_IT_regions.geojson")
regioni.head()

reg_name  reg_istat_code_num reg_istat_code  \
0                      Piemonte                   1             01   
1  Valle d'Aosta/Vallée d'Aoste                   2             02   
2                     Lombardia                   3             03   
3  Trentino-Alto Adige/Südtirol                   4             04   
4                        Veneto                   5             05   

                                            geometry  
0  POLYGON ((7.13605 45.27996, 7.13601 45.28040, ...  
1  POLYGON ((7.73455 45.92365, 7.73590 45.92744, ...  
2  MULTIPOLYGON (((8.57964 45.75172, 8.57532 45.7...  
3  POLYGON ((12.01396 46.55091, 12.01376 46.55077...  
4  POLYGON ((10.63538 45.53543, 10.63228 45.56846...

In [4]:
date=dati_reg.data.unique()
date

array(['2020-02-24 18:00:00', '2020-02-25 18:00:00',
       '2020-02-26 18:00:00', '2020-02-27 18:00:00',
       '2020-02-28 18:00:00', '2020-02-29 17:00:00',
       '2020-03-01 17:00:00', '2020-03-02 18:00:00',
       '2020-03-03 18:00:00', '2020-03-04 17:00:00',
       '2020-03-05 17:00:00', '2020-03-06 17:00:00',
       '2020-03-07 18:00:00', '2020-03-08 18:00:00',
       '2020-03-09 18:00:00', '2020-03-10 18:00:00',
       '2020-03-11 17:00:00', '2020-03-12 17:00:00',
       '2020-03-13 17:00:00', '2020-03-14 17:00:00',
       '2020-03-15 17:00:00', '2020-03-16 17:00:00',
       '2020-03-17 17:00:00', '2020-03-18 17:00:00',
       '2020-03-19 17:00:00', '2020-03-20 17:00:00',
       '2020-03-21 17:00:00', '2020-03-22 17:00:00'], dtype=object)

In [5]:
dati_reg_cln=dati_reg.loc[(dati_reg.data==date[-1])&(dati_reg.denominazione_regione!='In fase di definizione/aggiornamento')]
dati_reg_cln.sort_values('denominazione_regione',axis=0,inplace=True)
dati_reg_cln.head()

C:\Users\simone\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


data stato  codice_regione denominazione_regione  \
567  2020-03-22 17:00:00   ITA              13               Abruzzo   
568  2020-03-22 17:00:00   ITA              17            Basilicata   
570  2020-03-22 17:00:00   ITA              18              Calabria   
571  2020-03-22 17:00:00   ITA              15              Campania   
572  2020-03-22 17:00:00   ITA               8        Emilia Romagna   

           lat       long  ricoverati_con_sintomi  terapia_intensiva  \
567  42.351222  13.398438                     218                 49   
568  40.639471  15.805148                      13                 10   
570  38.905976  16.594402                      77                 17   
571  40.839566  14.250850                     243                 99   
572  44.494367  11.341721                    2429                269   

     totale_ospedalizzati  isolamento_domiciliare  \
567                   267                     272   
568                    23                      58   
570                    94                     166   
571                   342                     524   
572                  2698                    3692   

     totale_attualmente_positivi  nuovi_attualmente_positivi  dimessi_guariti  \
567                          539                          45               15   
568                           81                          15                0   
570                          260                          35                5   
571                          866                          73               41   
572                         6390                         729              349   

     deceduti  totale_casi  tamponi  
567        33          587     3375  
568         0           81      643  
570         8          273     3666  
571        29          936     4943  
572       816         7555    28022

In [6]:
dati_pr_cln=dati_pr.loc[(dati_pr.data==date[-1])&(dati_pr.denominazione_provincia!='In fase di definizione/aggiornamento')]
dati_pr_cln.head()

data stato  codice_regione denominazione_regione  \
3456  2020-03-22 17:00:00   ITA              13               Abruzzo   
3457  2020-03-22 17:00:00   ITA              13               Abruzzo   
3458  2020-03-22 17:00:00   ITA              13               Abruzzo   
3459  2020-03-22 17:00:00   ITA              13               Abruzzo   
3461  2020-03-22 17:00:00   ITA              17            Basilicata   

      codice_provincia denominazione_provincia sigla_provincia        lat  \
3456                69                  Chieti              CH  42.351032   
3457                66                L'Aquila              AQ  42.351222   
3458                68                 Pescara              PE  42.464584   
3459                67                  Teramo              TE  42.658918   
3461                77                  Matera              MT  40.667512   

           long  totale_casi  
3456  14.167546          102  
3457  13.398438           38  
3458  14.213648          334  
3459  13.704400          113  
3461  16.597924           16

In [7]:
l=regioni.reg_name.unique()
l2=dati_reg.denominazione_regione.unique()
list_dif = [i for i in l2 if i not in l]
list_dif

['P.A. Bolzano',
 'Emilia Romagna',
 'Friuli Venezia Giulia',
 'P.A. Trento',
 "Valle d'Aosta"]

In [8]:
dati_reg_cln.denominazione_regione.nunique(), dati_reg_cln.codice_regione.nunique()

(21, 20)

In [10]:
#regioni.sort_values('reg_istat_code_num',axis=0,inplace=True)
#regioni

reg_name  reg_istat_code_num reg_istat_code  \
0                       Piemonte                   1             01   
1   Valle d'Aosta/Vallée d'Aoste                   2             02   
2                      Lombardia                   3             03   
3   Trentino-Alto Adige/Südtirol                   4             04   
4                         Veneto                   5             05   
5          Friuli-Venezia Giulia                   6             06   
6                        Liguria                   7             07   
7                 Emilia-Romagna                   8             08   
8                        Toscana                   9             09   
9                         Umbria                  10             10   
10                        Marche                  11             11   
11                         Lazio                  12             12   
12                       Abruzzo                  13             13   
13                        Molise                  14             14   
14                      Campania                  15             15   
15                        Puglia                  16             16   
16                    Basilicata                  17             17   
17                      Calabria                  18             18   
18                       Sicilia                  19             19   
19                      Sardegna                  20             20   

                                             geometry  
0   POLYGON ((7.13605 45.27996, 7.13601 45.28040, ...  
1   POLYGON ((7.73455 45.92365, 7.73590 45.92744, ...  
2   MULTIPOLYGON (((8.57964 45.75172, 8.57532 45.7...  
3   POLYGON ((12.01396 46.55091, 12.01376 46.55077...  
4   POLYGON ((10.63538 45.53543, 10.63228 45.56846...  
5   MULTIPOLYGON (((13.51691 46.38301, 13.51750 46...  
6   MULTIPOLYGON (((7.55166 43.89429, 7.56264 43.9...  
7   MULTIPOLYGON (((9.33258 44.73504, 9.33167 44.7...  
8   MULTIPOLYGON (((9.89786 44.16359, 9.89451 44.1...  
9   MULTIPOLYGON (((13.15849 42.65425, 13.15764 42...  
10  POLYGON ((12.40021 43.50977, 12.39933 43.50953...  
11  MULTIPOLYGON (((11.81091 42.80692, 11.81269 42...  
12  MULTIPOLYGON (((13.94102 41.68797, 13.94048 41...  
13  POLYGON ((14.41933 41.43515, 14.41251 41.44122...  
14  MULTIPOLYGON (((14.12527 41.50737, 14.13202 41...  
15  MULTIPOLYGON (((15.09831 41.39057, 15.09656 41...  
16  MULTIPOLYGON (((15.46575 40.63359, 15.46593 40...  
17  MULTIPOLYGON (((15.97395 39.46742, 15.97243 39...  
18  MULTIPOLYGON (((12.90787 38.02511, 12.90945 38...  
19  MULTIPOLYGON (((8.36788 40.49643, 8.36639 40.4...

In [9]:
regioni_plt = regioni[["reg_name", "geometry"]].set_index("reg_name")
regioni_plt.sort_values('reg_name',inplace=True)
regioni_plt

geometry
reg_name                                                                       
Abruzzo                       MULTIPOLYGON (((13.94102 41.68797, 13.94048 41...
Basilicata                    MULTIPOLYGON (((15.46575 40.63359, 15.46593 40...
Calabria                      MULTIPOLYGON (((15.97395 39.46742, 15.97243 39...
Campania                      MULTIPOLYGON (((14.12527 41.50737, 14.13202 41...
Emilia-Romagna                MULTIPOLYGON (((9.33258 44.73504, 9.33167 44.7...
Friuli-Venezia Giulia         MULTIPOLYGON (((13.51691 46.38301, 13.51750 46...
Lazio                         MULTIPOLYGON (((11.81091 42.80692, 11.81269 42...
Liguria                       MULTIPOLYGON (((7.55166 43.89429, 7.56264 43.9...
Lombardia                     MULTIPOLYGON (((8.57964 45.75172, 8.57532 45.7...
Marche                        POLYGON ((12.40021 43.50977, 12.39933 43.50953...
Molise                        POLYGON ((14.41933 41.43515, 14.41251 41.44122...
Piemonte                      POLYGON ((7.13605 45.27996, 7.13601 45.28040, ...
Puglia                        MULTIPOLYGON (((15.09831 41.39057, 15.09656 41...
Sardegna                      MULTIPOLYGON (((8.36788 40.49643, 8.36639 40.4...
Sicilia                       MULTIPOLYGON (((12.90787 38.02511, 12.90945 38...
Toscana                       MULTIPOLYGON (((9.89786 44.16359, 9.89451 44.1...
Trentino-Alto Adige/Südtirol  POLYGON ((12.01396 46.55091, 12.01376 46.55077...
Umbria                        MULTIPOLYGON (((13.15849 42.65425, 13.15764 42...
Valle d'Aosta/Vallée d'Aoste  POLYGON ((7.73455 45.92365, 7.73590 45.92744, ...
Veneto                        POLYGON ((10.63538 45.53543, 10.63228 45.56846...

In [24]:
dati_reg_dict=dati_reg_cln.groupby(['denominazione_regione'])['deceduti'].apply(lambda x: int(x.values))

In [25]:
dati_reg_dict['Trentino-Alto Adige/Südtirol']=dati_reg_dict['P.A. Bolzano']+dati_reg_dict['P.A. Trento']

In [26]:
dati_reg_dict.drop(['P.A. Bolzano','P.A. Trento'],inplace=True)

In [27]:
dati_reg_dict.sort_index(inplace=True)

In [28]:
dati_reg_dict.rename({'P.A. Trento':'Trentino-Alto Adige/Südtirol',
                      'Valle d\'Aosta':'Valle d\'Aosta/Vallée d\'Aoste',
                      'Emilia Romagna': 'Emilia-Romagna',
                          'Friuli Venezia Giulia': 'Friuli-Venezia Giulia'},inplace=True)

In [15]:
dati_reg_dict

denominazione_regione
Abruzzo                           587
Basilicata                         81
Calabria                          273
Campania                          936
Emilia-Romagna                   7555
Friuli-Venezia Giulia             874
Lazio                            1383
Liguria                          1665
Lombardia                       27206
Marche                           2421
Molise                             66
Piemonte                         4420
Puglia                            786
Sardegna                          339
Sicilia                           630
Toscana                          2277
Trentino-Alto Adige/Südtirol     1632
Umbria                            521
Valle d'Aosta/Vallée d'Aoste      364
Veneto                           5122
Name: totale_casi, dtype: int64

In [29]:
linear = cm.linear.Paired_08.scale(dati_reg_cln.deceduti.min(), dati_reg_cln.deceduti.max())#.to_step(n=15)
linear.caption = 'Numero di deceduti per regione'
linear

In [30]:
m = folium.Map(location=[42.351032,14.167546], tiles='cartodbpositron', zoom_start=5)

folium.GeoJson(
    regioni_plt,
    style_function=lambda feature: {
    'fillColor': linear(dati_reg_dict[feature['id']]),
    'opacity':1,
    'fill_opacity':0.9,
    'color' : 'black',
    'weight' : 0.3,
    'dashArray' : 0,
        }
    ).add_to(m)
for idx, row in dati_reg_cln.iterrows():
    popup = 'In {} sono decedute {} persone'.format(str(dati_reg_cln.denominazione_regione.loc[idx]),
                                                                      str(dati_reg_cln.deceduti.loc[idx]))
    folium.Marker([row['lat'], row['long']],
                        radius=5, color='green', opacity=0.6,
                 tooltip=popup).add_to(m)
m.add_child(linear)
m

In [155]:
m.save('regioni_interattiva.html')